In [1]:
import h5py
import os
import numpy as np
import pandas as pd
from collections import OrderedDict
import modisco
import tqdm
tqdm.tqdm_notebook()

TF-MoDISco is using the TensorFlow backend.
/users/avanti/anaconda3/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/users/avanti/anaconda3/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/users/avanti/anaconda3/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/users/avanti/anaconda3/lib/python3

|<bar/>| 0/? [00:00<?, ?it/s]

In [2]:
# Constants
shap_scores_base = "/users/amtseng/gata1/results/shap_scores/cutnrun_proftransfer"
shap_scores_path = os.path.join(shap_scores_base, "cutnrun_gata1_proftransfer_sequence_shap_scores.h5")

pred_perfs_base = "/users/amtseng/gata1/results/peak_predictions/cutnrun_proftransfer"
profile_pred_perfs_path = os.path.join(pred_perfs_base, "cutnrun_gata1_proftransfer_profile_preds_perf.h5")
sequence_pred_perfs_path = os.path.join(pred_perfs_base, "cutnrun_gata1_proftransfer_sequence_preds_perf.h5")

In [3]:
outbase = "/users/amtseng/gata1/results/tfmodisco/cutnrun_proftransfer"
tfm_outpath = os.path.join(outbase, "cutnrun_gata1_proftransfer_tfm.h5")
seqlets_outpath = os.path.join(outbase, "cutnrun_gata1_proftransfer_seqlets.fasta")
plots_outpath = os.path.join(outbase, "cutnrun_gata1_proftransfer_figs")


In [4]:
input_length = 1346
center_cut_size = 500

In [5]:

def rank_coordinates(
    profile_pred_perfs_path, sequence_pred_perfs_path, rank_key="norm_nll"
):
    """
    From the saved predictions/performance of each peak trained with the
    profile module and after training the sequence module, ranks the
    coordinates in order of improvement specified by `rank_key`. The rank
    key can be "norm_nll" or "jsd". Returns an N x 3 array of coordinates
    and a parallel N-array of value changes (sequence - profile), in
    ascending order. Improvements over tasks are averaged.
    """
    p_reader = h5py.File(profile_pred_perfs_path, "r")
    s_reader = h5py.File(sequence_pred_perfs_path, "r")
    
    print("Checking coordinates all identical...")
    assert np.all(p_reader["coords"]["coords_chrom"][:] == s_reader["coords"]["coords_chrom"][:])
    assert np.all(p_reader["coords"]["coords_start"][:] == s_reader["coords"]["coords_start"][:])
    assert np.all(p_reader["coords"]["coords_end"][:] == s_reader["coords"]["coords_end"][:])
    coords = np.empty((len(p_reader["coords"]["coords_chrom"]), 3), dtype="object")
    coords[:, 0] = p_reader["coords"]["coords_chrom"][:].astype(str)
    coords[:, 1] = p_reader["coords"]["coords_start"][:]
    coords[:, 2] = p_reader["coords"]["coords_end"][:]
    
    print("Extracting metrics...")
    if rank_key == "jsd":
        p_metrics = p_reader["performance"]["jsd"][:]
        s_metrics = s_reader["performance"]["jsd"][:]  # Shape: N x T
    else:
        avg_counts = np.mean(p_reader["predictions"]["true_counts"][:], axis=2)  # Shape: N x T (average strands)
        p_metrics = p_reader["performance"]["nll"][:] / avg_counts
        s_metrics = s_reader["performance"]["nll"][:] / avg_counts
    
    print("Sorting coordinates...")
    diff = s_metrics - p_metrics
    avg_diff = np.mean(diff, axis=1)  # Shape: N (average tasks)
    sorted_inds = np.argsort(avg_diff)
    return coords[sorted_inds], avg_diff[sorted_inds]

In [6]:
def import_shap_scores(shap_scores_hdf5, center_cut_size, limit_coords):
    """
    Imports the SHAP scores, cuts them to `center_cut_size`, and
    only keeps coordinates that match those in the N x 3 array
    `limit_coords`. Returns N x L x 4 arrays of hypothetical scores,
    actual scores, input sequences, and coordinates (N x 3).
    """
    hyp_score_key = "hyp_scores"
    shap_reader = h5py.File(shap_scores_path, "r")
    
    # Read in coordinates from SHAP file
    shap_coords = np.empty((len(shap_reader["coords_chrom"]), 3), dtype=object)
    shap_coords[:, 0] = shap_reader["coords_chrom"][:].astype(str)
    shap_coords[:, 1] = shap_reader["coords_start"][:]
    shap_coords[:, 2] = shap_reader["coords_end"][:]
    
    # Identify which indices of the SHAP coords correspond to coordinates in the
    # specified coordinates
    shap_coords_table = pd.DataFrame(shap_coords, columns=["chrom", "start", "end"])
    limit_coords_table = pd.DataFrame(limit_coords, columns=["chrom", "start", "end"])
    
    subset_inds = shap_coords_table.reset_index().drop_duplicates(["chrom", "start", "end"]).merge(
        limit_coords_table.reset_index(), on=["chrom", "start", "end"]
    ).sort_values("index_y")["index_x"].values
    
    subset_inds = np.unique(subset_inds)

    # For defining shapes
    num_seqs = len(subset_inds)
    input_length = shap_reader[hyp_score_key].shape[1]
    if not center_cut_size:
        center_cut_size = input_length
    cut_start = (input_length // 2) - (center_cut_size // 2)
    cut_end = cut_start + center_cut_size

    # For batching up data loading
    batch_size = min(1000, num_seqs)
    num_batches = int(np.ceil(num_seqs / batch_size))

    # Read in hypothetical scores and input sequences in batches
    hyp_scores = np.empty((num_seqs, center_cut_size, 4))
    act_scores = np.empty((num_seqs, center_cut_size, 4))
    one_hot_seqs = np.empty((num_seqs, center_cut_size, 4))
    coords = np.empty((num_seqs, 3), dtype=object)

    for i in tqdm.notebook.trange(num_batches, desc="Importing SHAP scores"):
        batch_slice = slice(i * batch_size, (i + 1) * batch_size)
        hyp_score_batch = shap_reader[hyp_score_key][
            subset_inds[batch_slice], cut_start:cut_end
        ]
        one_hot_seq_batch = shap_reader["input_seqs"][
            subset_inds[batch_slice], cut_start:cut_end
        ]
        chrom_batch = shap_reader["coords_chrom"][subset_inds[batch_slice]].astype(str)
        start_batch = shap_reader["coords_start"][subset_inds[batch_slice]]
        end_batch = shap_reader["coords_end"][subset_inds[batch_slice]]
        hyp_scores[batch_slice] = hyp_score_batch
        one_hot_seqs[batch_slice] = one_hot_seq_batch
        act_scores[batch_slice] = hyp_score_batch * one_hot_seq_batch
        coords[batch_slice, 0] = chrom_batch
        coords[batch_slice, 1] = start_batch
        coords[batch_slice, 2] = end_batch

    shap_reader.close()

    # Remove any examples in which the input sequence is not all ACGT
    mask = np.sum(one_hot_seqs, axis=(1, 2)) == center_cut_size

    return hyp_scores[mask], act_scores[mask], one_hot_seqs[mask], coords[mask]

In [7]:
def run_tfmodisco(hyp_scores, act_scores, input_seqs, outfile, seqfile, plotdir):
    """
    Runs TF-MoDISco.
    """
    task_to_hyp_scores, task_to_act_scores = OrderedDict(), OrderedDict()
    task_to_hyp_scores["task0"] = hyp_scores
    task_to_act_scores["task0"] = act_scores

    # Construct workflow pipeline
    tfm_workflow = modisco.tfmodisco_workflow.workflow.TfModiscoWorkflow(
        sliding_window_size=21,
        flank_size=10,
        target_seqlet_fdr=0.05,
        seqlets_to_patterns_factory=modisco.tfmodisco_workflow.seqlets_to_patterns.TfModiscoSeqletsToPatternsFactory(
            trim_to_window_size=30,
            initial_flank_to_add=10,
            kmer_len=8,
            num_gaps=3,
            num_mismatches=2,
            final_min_cluster_size=60
        )
    )

    # Move to output directory to do work
    cwd = os.getcwd()
    os.makedirs(os.path.dirname(outfile), exist_ok=True)
    os.chdir(os.path.dirname(outfile))

    tfm_results = tfm_workflow(
        task_names=list(task_to_act_scores.keys()),
        contrib_scores=task_to_act_scores,
        hypothetical_contribs=task_to_hyp_scores,
        one_hot=input_seqs,
        plot_save_dir=plotdir
    )

    os.chdir(cwd)
    print("Saving results to %s" % outfile)
    with h5py.File(outfile, "w") as f:
        tfm_results.save_hdf5(f)

    print("Saving seqlets to %s" % seqfile)
    seqlets = \
        tfm_results.metacluster_idx_to_submetacluster_results[0].seqlets
    bases = np.array(["A", "C", "G", "T"])
    with open(seqfile, "w") as f:
        for seqlet in seqlets:
            sequence = "".join(
                bases[np.argmax(seqlet["sequence"].fwd, axis=-1)]
            )
            example_index = seqlet.coor.example_idx
            start, end = seqlet.coor.start, seqlet.coor.end
            f.write(">example%d:%d-%d\n" % (example_index, start, end))
            f.write(sequence + "\n")

In [8]:
ranked_coords, metric_change = rank_coordinates(profile_pred_perfs_path, sequence_pred_perfs_path)

OSError: Unable to open file (unable to open file: name = '/users/amtseng/gata1/results/peak_predictions/cutnrun_proftransfer/cutnrun_gata1_proftransfer_profile_preds_perf.h5', errno = 13, error message = 'Permission denied', flags = 0, o_flags = 0)

In [9]:
top_coords = ranked_coords[metric_change < 0]

NameError: name 'ranked_coords' is not defined

In [10]:
hyp_scores, act_scores, input_seqs, shap_coords = import_shap_scores(
    shap_scores_path, center_cut_size, top_coords
)

NameError: name 'top_coords' is not defined